# STEP1

In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import col, explode, from_unixtime


# Receipts Data 

In [0]:
df = spark.read.json('abfss://samartechdev01adlsgen2@samartechdev01adlsgen2.dfs.core.windows.net/sandbox/receipts.json.gz')
df.show(2)

+--------------------+-----------------+-----------------------+---------------+---------------+---------------+---------------+-----------------+------------+---------------+------------------+----------------------+--------------------+----------+--------------------+
|                 _id|bonusPointsEarned|bonusPointsEarnedReason|     createDate|    dateScanned|   finishedDate|     modifyDate|pointsAwardedDate|pointsEarned|   purchaseDate|purchasedItemCount|rewardsReceiptItemList|rewardsReceiptStatus|totalSpent|              userId|
+--------------------+-----------------+-----------------------+---------------+---------------+---------------+---------------+-----------------+------------+---------------+------------------+----------------------+--------------------+----------+--------------------+
|{5ff1e1eb0a720f05...|              500|   Receipt number 2 ...|{1609687531000}|{1609687531000}|{1609687531000}|{1609687536000}|  {1609687531000}|       500.0|{1609632000000}|            

In [0]:
df.dtypes

[('_id', 'struct<$oid:string>'),
 ('bonusPointsEarned', 'bigint'),
 ('bonusPointsEarnedReason', 'string'),
 ('createDate', 'struct<$date:bigint>'),
 ('dateScanned', 'struct<$date:bigint>'),
 ('finishedDate', 'struct<$date:bigint>'),
 ('modifyDate', 'struct<$date:bigint>'),
 ('pointsAwardedDate', 'struct<$date:bigint>'),
 ('pointsEarned', 'string'),
 ('purchaseDate', 'struct<$date:bigint>'),
 ('purchasedItemCount', 'bigint'),
 ('rewardsReceiptItemList',
  'array<struct<barcode:string,brandCode:string,competitiveProduct:boolean,competitorRewardsGroup:string,deleted:boolean,description:string,discountedItemPrice:string,finalPrice:string,itemNumber:string,itemPrice:string,metabriteCampaignId:string,needsFetchReview:boolean,needsFetchReviewReason:string,originalFinalPrice:string,originalMetaBriteBarcode:string,originalMetaBriteDescription:string,originalMetaBriteItemPrice:string,originalMetaBriteQuantityPurchased:bigint,originalReceiptItemText:string,partnerItemId:string,pointsEarned:string

- **After loading the receipts dataset, transforming the raw data to form a structured format.**
- **Instead of saving the data to the data warehouse, for now I am saving the flattened dataframe into a Temp Table**

In [0]:
schema = StructType([
    StructField('_id', StructType([StructField('$oid', StringType(), True)])),
    StructField('bonusPointsEarned', LongType(), True),
    StructField('bonusPointsEarnedReason', StringType(), True),
    StructField('createDate', StructType([StructField('$date', LongType(), True)])),
    StructField('dateScanned', StructType([StructField('$date', LongType(), True)])),
    StructField('finishedDate', StructType([StructField('$date', LongType(), True)])),
    StructField('modifyDate', StructType([StructField('$date', LongType(), True)])),
    StructField('pointsAwardedDate', StructType([StructField('$date', LongType(), True)])),
    StructField('pointsEarned', StringType(), True),
    StructField('purchaseDate', StructType([StructField('$date', LongType(), True)])),
    StructField('purchasedItemCount', LongType(), True),
    StructField('rewardsReceiptItemList', ArrayType(StructType([
        StructField('barcode', StringType(), True),
        StructField('brandCode', StringType(), True),
        StructField('competitiveProduct', BooleanType(), True),
        StructField('competitorRewardsGroup', StringType(), True),
        StructField('deleted', BooleanType(), True),
        StructField('description', StringType(), True),
        StructField('discountedItemPrice', StringType(), True),
        StructField('finalPrice', StringType(), True),
        StructField('itemNumber', StringType(), True),
        StructField('itemPrice', StringType(), True),
        StructField('metabriteCampaignId', StringType(), True),
        StructField('needsFetchReview', BooleanType(), True),
        StructField('needsFetchReviewReason', StringType(), True),
        StructField('originalFinalPrice', StringType(), True),
        StructField('originalMetaBriteBarcode', StringType(), True),
        StructField('originalMetaBriteDescription', StringType(), True),
        StructField('originalMetaBriteItemPrice', StringType(), True),
        StructField('originalMetaBriteQuantityPurchased', LongType(), True),
        StructField('originalReceiptItemText', StringType(), True),
        StructField('partnerItemId', StringType(), True),
        StructField('pointsEarned', StringType(), True),
        StructField('pointsNotAwardedReason', StringType(), True),
        StructField('pointsPayerId', StringType(), True),
        StructField('preventTargetGapPoints', BooleanType(), True),
        StructField('priceAfterCoupon', StringType(), True),
        StructField('quantityPurchased', LongType(), True),
        StructField('rewardsGroup', StringType(), True),
        StructField('rewardsProductPartnerId', StringType(), True),
        StructField('targetPrice', StringType(), True),
        StructField('userFlaggedBarcode', StringType(), True),
        StructField('userFlaggedDescription', StringType(), True),
        StructField('userFlaggedNewItem', BooleanType(), True),
        StructField('userFlaggedPrice', StringType(), True),
        StructField('userFlaggedQuantity', LongType(), True),
    ]), True)),
    StructField('rewardsReceiptStatus', StringType(), True),
    StructField('totalSpent', StringType(), True),
    StructField('userId', StringType(), True)
])

In [0]:
# Flattening the nested fields and convert timestamps for the date fields
df_flat = df.withColumn('createDate', from_unixtime(col('createDate.$date') / 1000).cast('timestamp')) \
            .withColumn('dateScanned', from_unixtime(col('dateScanned.$date') / 1000).cast('timestamp')) \
            .withColumn('finishedDate', from_unixtime(col('finishedDate.$date') / 1000).cast('timestamp')) \
            .withColumn('modifyDate', from_unixtime(col('modifyDate.$date') / 1000).cast('timestamp')) \
            .withColumn('pointsAwardedDate', from_unixtime(col('pointsAwardedDate.$date') / 1000).cast('timestamp')) \
            .withColumn('purchaseDate', from_unixtime(col('purchaseDate.$date') / 1000).cast('timestamp')) \
            .withColumn('id', col('_id.$oid'))

# Explode the rewardsReceiptItemList array
df_flat = df_flat.withColumn('item', explode('rewardsReceiptItemList'))

# Selecting the required fields, including fields from the exploded array
df_flat = df_flat.select(
    col('id'),
    col('bonusPointsEarned'),
    col('bonusPointsEarnedReason'),
    col('createDate'),
    col('dateScanned'),
    col('finishedDate'),
    col('modifyDate'),
    col('pointsAwardedDate'),
    col('pointsEarned'),
    col('purchaseDate'),
    col('purchasedItemCount'),
    col('rewardsReceiptStatus'),
    col('totalSpent'),
    col('userId'),
    col('item.barcode').alias('barcode'),
    col('item.brandCode').alias('brandCode'),
    col('item.competitiveProduct').alias('competitiveProduct'),
    col('item.competitorRewardsGroup').alias('competitorRewardsGroup'),
    col('item.deleted').alias('deleted'),
    col('item.description').alias('description'),
    col('item.discountedItemPrice').alias('discountedItemPrice'),
    col('item.finalPrice').alias('finalPrice'),
    col('item.itemNumber').alias('itemNumber'),
    col('item.itemPrice').alias('itemPrice'),
    col('item.metabriteCampaignId').alias('metabriteCampaignId'),
    col('item.needsFetchReview').alias('needsFetchReview'),
    col('item.needsFetchReviewReason').alias('needsFetchReviewReason'),
    col('item.originalFinalPrice').alias('originalFinalPrice'),
    col('item.originalMetaBriteBarcode').alias('originalMetaBriteBarcode'),
    col('item.originalMetaBriteDescription').alias('originalMetaBriteDescription'),
    col('item.originalMetaBriteItemPrice').alias('originalMetaBriteItemPrice'),
    col('item.originalMetaBriteQuantityPurchased').alias('originalMetaBriteQuantityPurchased'),
    col('item.originalReceiptItemText').alias('originalReceiptItemText'),
    col('item.partnerItemId').alias('partnerItemId'),
    col('item.pointsEarned').alias('pointsEarned'),
    col('item.pointsNotAwardedReason').alias('pointsNotAwardedReason'),
    col('item.pointsPayerId').alias('pointsPayerId'),
    col('item.preventTargetGapPoints').alias('preventTargetGapPoints'),
    col('item.priceAfterCoupon').alias('priceAfterCoupon'),
    col('item.quantityPurchased').alias('quantityPurchased'),
    col('item.rewardsGroup').alias('rewardsGroup'),
    col('item.rewardsProductPartnerId').alias('rewardsProductPartnerId'),
    col('item.targetPrice').alias('targetPrice'),
    col('item.userFlaggedBarcode').alias('userFlaggedBarcode'),
    col('item.userFlaggedDescription').alias('userFlaggedDescription'),
    col('item.userFlaggedNewItem').alias('userFlaggedNewItem'),
    col('item.userFlaggedPrice').alias('userFlaggedPrice'),
    col('item.userFlaggedQuantity').alias('userFlaggedQuantity')
)

In [0]:
df_flat.createOrReplaceTempView('receipts')

# Brands Data

In [0]:
df2 = spark.read.json('abfss://samartechdev01adlsgen2@samartechdev01adlsgen2.dfs.core.windows.net/sandbox/brands.json.gz')
df2.show(2)

+--------------------+------------+---------+---------+------------+--------------------+--------------------+--------+
|                 _id|     barcode|brandCode| category|categoryCode|                 cpg|                name|topBrand|
+--------------------+------------+---------+---------+------------+--------------------+--------------------+--------+
|{601ac115be37ce2e...|511111019862|     NULL|   Baking|      BAKING|{{601ac114be37ce2...|test brand @16123...|   false|
|{601c5460be37ce2e...|511111519928|STARBUCKS|Beverages|   BEVERAGES|{{5332f5fbe4b03c9...|           Starbucks|   false|
+--------------------+------------+---------+---------+------------+--------------------+--------------------+--------+
only showing top 2 rows



In [0]:
df2.dtypes

[('_id', 'struct<$oid:string>'),
 ('barcode', 'string'),
 ('brandCode', 'string'),
 ('category', 'string'),
 ('categoryCode', 'string'),
 ('cpg', 'struct<$id:struct<$oid:string>,$ref:string>'),
 ('name', 'string'),
 ('topBrand', 'boolean')]

In [0]:

# Flatten the nested fields
df2_flat = df2.withColumn('id', col('_id.$oid')) \
              .withColumn('cpg_id', col('cpg.$id.$oid')) \
              .withColumn('cpg_ref', col('cpg.$ref')) \
              .drop('cpg')

# Select the required fields
df2_flat = df2_flat.select(
    'id',
    'barcode',
    'brandCode',
    'category',
    'categoryCode',
    'cpg_id',
    'cpg_ref',
    'name',
    'topBrand'
)


In [0]:
df2_flat.createOrReplaceTempView('brands')

# Users Data

In [0]:
df3 = spark.read.json('abfss://samartechdev01adlsgen2@samartechdev01adlsgen2.dfs.core.windows.net/sandbox/users.json.gz')
df3.show(2)

+--------------------+--------------------+------+---------------+---------------+--------+------------+-----+
|     _corrupt_record|                 _id|active|    createdDate|      lastLogin|    role|signUpSource|state|
+--------------------+--------------------+------+---------------+---------------+--------+------------+-----+
|users.json       ...|                NULL|  NULL|           NULL|           NULL|    NULL|        NULL| NULL|
|                NULL|{5ff1e194b6a9d73a...|  true|{1609687444800}|{1609687537858}|consumer|       Email|   WI|
+--------------------+--------------------+------+---------------+---------------+--------+------------+-----+
only showing top 2 rows



In [0]:
df3.dtypes

[('_corrupt_record', 'string'),
 ('_id', 'struct<$oid:string>'),
 ('active', 'boolean'),
 ('createdDate', 'struct<$date:bigint>'),
 ('lastLogin', 'struct<$date:bigint>'),
 ('role', 'string'),
 ('signUpSource', 'string'),
 ('state', 'string')]

In [0]:
# Filter and drop the '_corrupt_record' attribute
df3_clean = df3.filter(df3['_corrupt_record'].isNull()).drop('_corrupt_record')


In [0]:
# Flattening the nested fields and convert timestamps
df3_flat = df3_clean.withColumn('id', col('_id.$oid')) \
                    .withColumn('createdDate', from_unixtime(col('createdDate.$date') / 1000).cast('timestamp')) \
                    .withColumn('lastLogin', from_unixtime(col('lastLogin.$date') / 1000).cast('timestamp'))

# Selecting the required fields
df3_flat = df3_flat.select(
    'id',
    'active',
    'createdDate',
    'lastLogin',
    'role',
    'signUpSource',
    'state'
)

In [0]:
df3_flat.createOrReplaceTempView('users')

In [0]:
%sql
-- just for displaying purposes
select * from receipts


id bonusPointsEarned bonusPointsEarnedReason createDate dateScanned finishedDate modifyDate pointsAwardedDate pointsEarned purchaseDate purchasedItemCount rewardsReceiptStatus totalSpent userId barcode brandCode competitiveProduct competitorRewardsGroup deleted description discountedItemPrice finalPrice itemNumber itemPrice metabriteCampaignId needsFetchReview needsFetchReviewReason originalFinalPrice originalMetaBriteBarcode originalMetaBriteDescription originalMetaBriteItemPrice originalMetaBriteQuantityPurchased originalReceiptItemText partnerItemId pointsEarned pointsNotAwardedReason pointsPayerId preventTargetGapPoints priceAfterCoupon quantityPurchased rewardsGroup rewardsProductPartnerId targetPrice userFlaggedBarcode userFlaggedDescription userFlaggedNewItem userFlaggedPrice userFlaggedQuantity 5ff1e1eb0a720f0523000575 500 Receipt number 2 completed, bonus point schedule DEFAULT (5cefdcacf3693e0b50e83a36) 2021-01-03T15:25:31Z 2021-01-03T15:25:31Z 2021-01-03T15:25:31Z 2021-01-03T15:25:36Z 2021-01-03T15:25:31Z 500.0 2021-01-03T00:00:00Z 5 FINISHED 26.00 5ff1e1eacfcf6c399c274ae6 4011 null null null null ITEM NOT FOUND null 26.00 null 26.00 null false null null null null null null null 1 null null null true null 5 null null null 4011 null true 26.00 5 5ff1e1bb0a720f052300056b 150 Receipt number 5 completed, bonus point schedule DEFAULT (5cefdcacf3693e0b50e83a36) 2021-01-03T15:24:43Z 2021-01-03T15:24:43Z 2021-01-03T15:24:43Z 2021-01-03T15:24:48Z 2021-01-03T15:24:43Z 150.0 2021-01-02T15:24:43Z 2 FINISHED 11.00 5ff1e194b6a9d73a3a9f1052 4011 null null null null ITEM NOT FOUND null 1 null 1 null null null null null null null null null 1 null null null null null 1 null null null null null null null null 5ff1e1bb0a720f052300056b 150 Receipt number 5 completed, bonus point schedule DEFAULT (5cefdcacf3693e0b50e83a36) 2021-01-03T15:24:43Z 2021-01-03T15:24:43Z 2021-01-03T15:24:43Z 2021-01-03T15:24:48Z 2021-01-03T15:24:43Z 150.0 2021-01-02T15:24:43Z 2 FINISHED 11.00 5ff1e194b6a9d73a3a9f1052 028400642255 null null null null DORITOS TORTILLA CHIP SPICY SWEET CHILI REDUCED FAT BAG 1 OZ null 10.00 null 10.00 null true USER_FLAGGED null null null null null null 2 null Action not allowed for user and CPG 5332f5fbe4b03c9a25efd0ba true null 1 DORITOS SPICY SWEET CHILI SINGLE SERVE 5332f5fbe4b03c9a25efd0ba null 028400642255 DORITOS TORTILLA CHIP SPICY SWEET CHILI REDUCED FAT BAG 1 OZ true 10.00 1 5ff1e1f10a720f052300057a 5 All-receipts receipt bonus 2021-01-03T15:25:37Z 2021-01-03T15:25:37Z null 2021-01-03T15:25:42Z null 5 2021-01-03T00:00:00Z 1 REJECTED 10.00 5ff1e1f1cfcf6c399c274b0b null null null null null null null null null null null false null null null null null null null 1 null null null true null null null null null 4011 null true 26.00 3 5ff1e1ee0a7214ada100056f 5 All-receipts receipt bonus 2021-01-03T15:25:34Z 2021-01-03T15:25:34Z 2021-01-03T15:25:34Z 2021-01-03T15:25:39Z 2021-01-03T15:25:34Z 5.0 2021-01-03T00:00:00Z 4 FINISHED 28.00 5ff1e1eacfcf6c399c274ae6 4011 null null null null ITEM NOT FOUND null 28.00 null 28.00 null false null null null null null null null 1 null null null true null 4 null null null 4011 null true 28.00 4 5ff1e1d20a7214ada1000561 5 All-receipts receipt bonus 2021-01-03T15:25:06Z 2021-01-03T15:25:06Z 2021-01-03T15:25:11Z 2021-01-03T15:25:11Z 2021-01-03T15:25:06Z 5.0 2021-01-02T15:25:06Z 2 FINISHED 1.00 5ff1e194b6a9d73a3a9f1052 4011 null null null null ITEM NOT FOUND null 1 null 1 null null null null null null null null null 1 null null null null null 1 null null null null null null null null 5ff1e1d20a7214ada1000561 5 All-receipts receipt bonus 2021-01-03T15:25:06Z 2021-01-03T15:25:06Z 2021-01-03T15:25:11Z 2021-01-03T15:25:11Z 2021-01-03T15:25:06Z 5.0 2021-01-02T15:25:06Z 2 FINISHED 1.00 5ff1e194b6a9d73a3a9f1052 1234 null null null null null null 2.56 null 2.56 null true USER_FLAGGED null null null null null null 2 null null null true null 3 null null null 1234 true 2.56 3 5ff1e1e40a7214ada1000566 750 Receipt

In [0]:
%sql
-- just for displaying purposes
select * from  brands


id barcode brandCode category categoryCode cpg_id cpg_ref name topBrand 601ac115be37ce2ead437551 511111019862 null Baking BAKING 601ac114be37ce2ead437550 Cogs test brand @1612366101024 false 601c5460be37ce2ead43755f 511111519928 STARBUCKS Beverages BEVERAGES 5332f5fbe4b03c9a25efd0ba Cogs Starbucks false 601ac142be37ce2ead43755d 511111819905 TEST BRANDCODE @1612366146176 Baking BAKING 601ac142be37ce2ead437559 Cogs test brand @1612366146176 false 601ac142be37ce2ead43755a 511111519874 TEST BRANDCODE @1612366146051 Baking BAKING 601ac142be37ce2ead437559 Cogs test brand @1612366146051 false 601ac142be37ce2ead43755e 511111319917 TEST BRANDCODE @1612366146827 Candy & Sweets CANDY_AND_SWEETS 5332fa12e4b03c9a25efd1e7 Cogs test brand @1612366146827 false 601ac142be37ce2ead43755b 511111719885 TEST BRANDCODE @1612366146091 Baking BAKING 601ac142be37ce2ead437559 Cogs test brand @1612366146091 false 601ac142be37ce2ead43755c 511111219897 TEST BRANDCODE @1612366146133 Baking BAKING 601ac142be37ce2ead437559 Cogs test brand @1612366146133 false 5cdad0f5166eb33eb7ce0faa 511111104810 J.L. KRAFT Condiments & Sauces null 559c2234e4b06aca36af13c6 Cogs J.L. Kraft null 5ab15636e4b0be0a89bb0b07 511111504412 CAMPBELLS HOME STYLE Canned Goods & Soups null 5a734034e4b0d58f376be874 Cogs Campbell's Home Style false 5c408e8bcd244a1fdb47aee7 511111504788 TEST Baking null 59ba6f1ce4b092b29c167346 Cogs test null 5f4bf556be37ce0b4491554d 511111516354 TEST BRANDCODE @1598813526777 Baking BAKING 5f4bf556be37ce0b44915549 Cogs test brand @1598813526777 null 57c08106e4b0718ff5fcb02c 511111102540 null null null 5332f5f2e4b03c9a25efd0aa Cpgs MorningStar null 588ba07be4b02187f85cdadd 511111201076 CALUMET Baking null 559c2234e4b06aca36af13c6 Cogs Calumet false 5d6413156d5f3b23d1bc790a 511111205012 511111205012 Magazines null 5d5d4fd16d5f3b23d1bc7905 Cogs Entertainment Weekly null 585a9611e4b03e62d1ce0e74 511111801801 AUNT JEMIMA SYRUP Breakfast & Cereal null 5332f5fbe4b03c9a25efd0ba Cogs AUNT JEMIMA Syrup false 57e5820ce4b0ac389136a311 511111202233 MOLSON Beer Wine Spirits null 5332f709e4b03c9a25efd0f1 Cpgs Molson Canadian false 5fb6adb8be37ce522e165cb8 511111817376 LOTRIMIN Health & Wellness HEALTHY_AND_WELLNESS 5d9b4f591dda2c6225a284aa Cogs Lotrimin® false 5f358338be37ce443bf9d55a 511111515319 TEST BRANDCODE @1597342520277 Baking BAKING 5f358338be37ce443bf9d557 Cogs test brand @1597342520277 null 5fb28549be37ce522e165cb5 511111317364 null Baking BAKING 5fb28549be37ce522e165cb4 Cogs test brand @1605535049181 false 592486bfe410d61fcea3d139 511111300700 ST IVES Beauty null 5332f5f6e4b03c9a25efd0b4 Cogs ST. IVES false 5c4699f387ff3577e203ea29 511111305125 CHRISIMAGE Baby null 55b62995e4b0d8e685c14213 Cogs Chris Image Test null 5da6071ea60b87376833e34d 511111005650 ALKA SELTZER Health & Wellness HEALTHY_AND_WELLNESS 5d9b4f591dda2c6225a284aa Cogs Alka-Seltzer® null 57ebc011e4b0ac389136a335 511111802129 JACK DANIEL'S BARBECUE Condiments & Sauces null 559c2234e4b06aca36af13c6 Cogs Jack Daniel's false 5332f5fee4b03c9a25efd0bd 511111303947 null null null 53e10d6368abd3c7065097cc Cpgs Bottled Starbucks null 5332fa7ce4b03c9a25efd22e 511111802914 null null null 5332f5ebe4b03c9a25efd0a8 Cpgs Full Throttle null 5e9f18bfbe37ce3e45b6a77f 511111914549 null Baking BAKING 5e9f12f5be37ce3e45b6a77e Cogs PopUp Brand A null 592486bee410d61fcea3d133 511111400769 MAGNUM Ice Cream Frozen null 5332f5f6e4b03c9a25efd0b4 Cogs MAGNUM Ice Cream false 5d66d71fa3a018093ab34728 511111105329 511111105329 Magazines null 5d5d4fd16d5f3b23d1bc7905 Cogs Elegant Homes Magazine null 5f493e72be37ce64d0ae36c6 511111316114 TEST BRANDCODE @1598635634882 Baking BAKING 5f493e72be37ce64d0ae36c2 Cogs test brand @1598635634882 null 5f4936ddbe37ce52f8314fd9 511111315957 null Baking BAKING 5f4936dcbe37ce52f8314fd8 Cogs test brand @1598633693011 null 57ebc2e7e4b0ac389136a34b 511111201915 TACO BELL Grocery null 559c2234e4b06aca36af13c6 Cogs Taco Bell false 5fd2a0aebe37ce49eb72c0ee 511111518112 null Baking BAKING 5fd2a0aebe37

In [0]:
%sql
-- just for displaying purposes
select * from users

id active createdDate lastLogin role signUpSource state 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1eacfcf6c399c274ae6 true 2021-01-03T15:25:30Z 2021-01-03T15:25:30Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1e8cfcf6c399c274ad9 true 2021-01-03T15:25:28Z 2021-01-03T15:25:28Z consumer Email WI 5ff1e1b7cfcf6c399c274a5a true 2021-01-03T15:24:39Z 2021-01-03T15:24:39Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1f1cfcf6c399c274b0b true 2021-01-03T15:25:37Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1eacfcf6c399c274ae6 true 2021-01-03T15:25:30Z 2021-01-03T15:25:30Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1eacfcf6c399c274ae6 true 2021-01-03T15:25:30Z 2021-01-03T15:25:30Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff1e1e4cfcf6c399c274ac3 true 2021-01-03T15:25:24Z 2021-01-03T15:25:24Z consumer Email WI 5ff1e1b4cfcf6c399c274a54 true 2021-01-03T15:24:36Z 2021-01-03T15:24:36Z consumer Email WI 5ff1e1eacfcf6c399c274ae6 true 2021-01-03T15:25:30Z 2021-01-03T15:25:30Z consumer Email WI 5ff1e194b6a9d73a3a9f1052 true 2021-01-03T15:24:04Z 2021-01-03T15:25:37Z consumer Email WI 5ff370c562fde912123a5e0e true 2021-01-04T19:47:17Z 2021-01-04T19:50:50Z consumer Email WI 5ff36d0362fde912123a5535 true 2021-01-04T19:31:15Z 2021-01-04T19:34:42Z consumer Email WI 5ff36d83135e7011bcb864d6 true 2021-01-04T19:33:23Z 2021-01-04T19:33:23Z consumer Email WI 5ff36c8862fde912123a538a true 2021-01-04T19:29:12Z 2021-01-04T19:29:13Z consumer Email WI 5ff370c562fde912123a5e0e true 2021-01-04T19:47:17Z 2021-01-04T19:50:50Z consumer Email WI 5ff36be7135e7011bcb856d3 true 2021-01-04T19:26:31Z 2021-01-04T19:29:52Z consumer Email WI 5ff36d0362fde912123a5535 true 2021-01-04T19:31:15Z 2021-01-04T19:34:42Z consumer Email WI 5ff36be7135e7011bcb856d3 true 2021-01-04T19:26:31Z 2021-01-04T19:29:52Z consumer Email WI 5ff36a3862fde912123a4460 true 2021-01-04T19:19:20Z 2021-01-04T19:23:05Z consumer Email WI 5ff36d0362fde912123a5535 true 2021-01-04T19:31:15Z 2021-01-04T19:34:42Z consumer Email WI 5ff36c8e135e7011bcb85da4 true 2021-01-04T19:29:18Z 2021-01-04T19:29:19Z consumer Email WI 5ff36a3862fde912123a4460 true 2021-01-04T19:19:20Z 2021-01-04T19:23:05Z consumer Email WI 5ff370c562fde912123a5e0e true 2021-01-04T19:47:17Z 2021-01-04T19:50:50Z consumer Email WI 5ff36a3862fde912123a4460 true 2021-01-04T19:19:20Z 2021-01-04T19:23:05Z consumer Email WI 5ff36a3862fde912123a4460 true 2021-01-04T19:19:20Z 2021-01-04T19:23:05Z consumer Email WI 5ff370c562fde912123a5e0e true 2021-01-04T19:47:17Z 2021-01-04T19:50:50Z consumer Email WI 5ff36a3862fde912123a4460 true 2021-01-04T19:19:20Z 2021-01-04T19:23:05Z consumer Email WI 5ff370c562fde912123a5e0e true 2021-01-04T19:47:17Z 2021-01-04T19:50:50Z consumer Email WI 5ff3711e62fde912123a620e true 2021-01-04T19:48:46Z 2021-01-04T19:48:46Z consumer Email WI 5ff36be7135e7011bcb856d3 true 2021-01-04T19:26:31Z 2021-01-04T19:29:52Z consumer Email WI 5ff4ce33c3d63511e2a484b6 true 2021-01-05T20:38:11Z 2021-01-05T20:39:55Z consumer Email WI 5ff473e7c1e2d0121a9b2697 true 2021-01-05T14:12:55Z 2021-01-05T14:12:55Z consumer Email WI 5ff47392c3d63511e2a47881 true 2021-01-05T14:11:30Z 2021-01-05T14:15:33Z consumer Email WI 5ff47392c3d63511e2a47881 true 2021-01-05T14:11:30Z 2021-01-05T14:15:33Z consumer Email WI 5ff4ce33c3d63511e2a484b6 true 2021-01-05T20:38:11Z 2021-01-05T20:39:55Z co

**In the data warehouse we can create partitions to the delta tables while creating them, this will improve query performance**

# STEP 2
# Queries

In [0]:
%sql
-- QUERY 1: Top 5 brands by receipts scanned for most recent month

SELECT b.id AS brand_id,
    b.name AS brand_name,
    COUNT(r.id) AS receipt_count
FROM receipts r
JOIN brands b 
ON r.barcode = b.barcode AND r.brandCode = b.brandCode
where YEAR(purchaseDate) = 2021
and Month(purchaseDate)=1
GROUP BY b.id, b.name
ORDER BY 
    receipt_count DESC
LIMIT 5;

brand_id brand_name receipt_count 585a972de4b03e62d1ce0e96 Tostitos 23 5a8c36dbe4b0ccf165fac9e9 Swanson 11 57d9580ee4b0ac389136a2b6 Cracker Barrel Cheese 10 5a8c344ae4b0ccf165fac9e5 Prego 7 5a8c35dde4b0ccf165fac9e6 Pepperidge Farm 5

In [0]:
%sql

-- Query 2: How does the ranking of the top 5 brands by receipts scanned for the recent month compare to the ranking for the previous month?
SELECT b.id AS brand_id,
    b.name AS brand_name,
    COUNT(r.id) AS receipt_count
FROM receipts r
JOIN brands b 
ON r.barcode = b.barcode AND r.brandCode = b.brandCode
where YEAR(purchaseDate) = 2020
and Month(purchaseDate)=12
GROUP BY b.id, b.name
ORDER BY 
    receipt_count DESC
LIMIT 5;

brand_id brand_name receipt_count

**Above query returned no results as there is no data for dec-2020 (here the most recent date is jan-2021)**

In [0]:
%sql
-- query3: When considering average spend from receipts with 'rewardsReceiptStatus’ of ‘Accepted’ or ‘Rejected’, which is greater?

SELECT
    rewardsReceiptStatus,
    AVG(CAST(totalSpent AS DECIMAL(10, 2))) AS avg_total_spent
FROM
    receipts
WHERE
    rewardsReceiptStatus IN ('FINISHED', 'REJECTED')
    AND TRY_CAST(totalSpent AS DECIMAL(10, 2)) IS NOT NULL  -- Ensure totalSpent is numeric
GROUP BY
    rewardsReceiptStatus
ORDER BY
    avg_total_spent DESC;

rewardsReceiptStatus avg_total_spent FINISHED 1244.793472 REJECTED 19.902500

In [0]:
%sql
-- query4: When considering total number of items purchased from receipts with 'rewardsReceiptStatus’ of ‘Accepted’ or ‘Rejected’, which is greater?
SELECT
    rewardsReceiptStatus,
    SUM(purchasedItemCount) AS total_items_purchased
FROM
    receipts
WHERE
    rewardsReceiptStatus IN ('FINISHED', 'REJECTED')
GROUP BY
    rewardsReceiptStatus
ORDER BY
    total_items_purchased DESC;


rewardsReceiptStatus total_items_purchased FINISHED 1364998 REJECTED 740

In [0]:
%sql
-- Query 5 : Which brand has the most spend among users who were created within the past 6 months?

-- Step 1: Find the maximum date in the dataset
WITH max_date_cte AS (
    SELECT MAX(purchaseDate) AS max_date
    FROM receipts
),

-- Step 2: Calculate the start date 6 months before the maximum date
date_variables AS (
    SELECT 
        max_date,
        DATE_SUB(max_date, 6*30) AS start_date -- Assuming roughly 30 days per month
    FROM max_date_cte
),

-- Step 3: Find the brand with the most spend among users created within the past 6 months
brand_spending AS (
    SELECT 
        b.id AS brand_id,
        b.name AS brand_name,
        SUM(r.totalSpent) AS total_spent
    FROM 
        users u
    JOIN 
        receipts r ON u.id = r.userId
    JOIN 
        brands b ON r.barcode = b.barcode AND r.brandCode = b.brandCode
    CROSS JOIN
        date_variables -- Cross join to access date variables
    WHERE 
        u.createdDate >= start_date
        AND r.purchaseDate BETWEEN start_date AND max_date
    GROUP BY 
        b.id, b.name
)

-- Step 4: Select the brand with the highest spend
SELECT 
    brand_id,
    brand_name,
    total_spent
FROM 
    brand_spending
ORDER BY 
    total_spent DESC
LIMIT 1;


brand_id brand_name total_spent 585a972de4b03e62d1ce0e96 Tostitos 23812.969999999998

In [0]:
%sql
-- Query6: Which brand has the most transactions among users who were created within the past 6 months?

-- Step 1: Find the maximum date in the dataset
WITH max_date_cte AS (
    SELECT MAX(purchaseDate) AS max_date
    FROM receipts
),

-- Step 2: Calculate the start date 6 months before the maximum date
date_variables AS (
    SELECT 
        max_date,
        DATE_SUB(max_date, 6*30) AS start_date -- Assuming roughly 30 days per month
    FROM max_date_cte
),

-- Step 3: Find the brand with the most transactions among users created within the past 6 months
brand_transactions AS (
    SELECT 
        b.id AS brand_id,
        b.name AS brand_name,
        COUNT(r.id) AS transaction_count
    FROM 
        users u
    JOIN 
        receipts r ON u.id = r.userId
    JOIN 
        brands b ON r.barcode = b.barcode AND r.brandCode = b.brandCode
    CROSS JOIN
        date_variables -- Cross join to access date variables
    WHERE 
        u.createdDate >= date_variables.start_date
        AND r.purchaseDate BETWEEN date_variables.start_date AND date_variables.max_date
    GROUP BY 
        b.id, b.name
)

-- Step 4: Select the brand with the highest number of transactions
SELECT 
    brand_id,
    brand_name,
    transaction_count
FROM 
    brand_transactions
ORDER BY 
    transaction_count DESC
LIMIT 1;


brand_id brand_name transaction_count 585a972de4b03e62d1ce0e96 Tostitos 43

## STEP 3
### some of the potential data quality issues from the data can be:
- **For the data quality isssues we can check for the missing values and the duplicates from the data, for critical data we can use default values in place where the data is missing**
- **Additionally we can check for the datatypes and alter the datatypes to form consistency over all the tables. I haven't really changed the datatypes and mostly utilized the data as it is. As we have a lot of date columns, we can check for the consistency in the Date formats**
- **Check for inconsistencies in the categorical data, from the 'category' column in brands data we have categories like "Dairy" and "Dairy & Refrigerated", this could be a potential issue with inconsistencies**
- **From the numerical columns in the receipts data we can check the summary of the data by calculating parameters like mean, median, standard deviation etc. Example: total spent has a max value of 4721.95 which could be a potential outlier**

In [0]:
%sql
SELECT COUNT(*)
FROM (
    SELECT *, COUNT(*) as cnt
    FROM users
    GROUP BY id, active, createdDate, lastLogin, role, signUpSource, state
    HAVING COUNT(*) > 1
) as duplicates;


count(1) 70